In [19]:
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
import seaborn as sns
import os
pd.set_option('display.max_columns', None)
import plotly.express as px


## Prepare the datasets

In [20]:
# If the data is already combined, read it
if os.path.exists('data/GTD.pkl'):
    df_orig = pd.read_pickle('data/GTD.pkl')
    
# Otherwise read both files and combine them
elif os.path.exists('data/GTD1.xlsx') and os.path.exists('data/GTD2.xlsx'):
    # Read data, ignore unicode errors
    df_1 = pd.read_excel('data/GTD1.xlsx')
    df_2 = pd.read_excel('data/GTD2.xlsx')
    # Append the two dataframes and save in a serialized format
    df = df_1.append(df_2)
    df.to_pickle('data/GTD.pkl')
else:
    print('Data not found, please put data in data folder')

In [21]:
df_orig.head()

eventid  iyear  imonth  iday approxdate  extended resolution  country  \
0  197000000001   1970       7     2        NaN         0        NaT       58   
1  197000000002   1970       0     0        NaN         0        NaT      130   
2  197001000001   1970       1     0        NaN         0        NaT      160   
3  197001000002   1970       1     0        NaN         0        NaT       78   
4  197001000003   1970       1     0        NaN         0        NaT      101   

          country_txt  region                   region_txt provstate  \
0  Dominican Republic       2  Central America & Caribbean  National   
1              Mexico       1                North America   Federal   
2         Philippines       5               Southeast Asia    Tarlac   
3              Greece       8               Western Europe    Attica   
4               Japan       4                    East Asia   Fukouka   

            city   latitude   longitude  specificity  vicinity location  \
0  Santo Domingo  18.456792  -69.951164          1.0         0      NaN   
1    Mexico city  19.371887  -99.086624          1.0         0      NaN   
2        Unknown  15.478598  120.599741          4.0         0      NaN   
3         Athens  37.997490   23.762728          1.0         0      NaN   
4        Fukouka  33.580412  130.396361          1.0         0      NaN   

  summary  crit1  crit2  crit3  doubtterr  alternative alternative_txt  \
0     NaN      1      1      1          0          NaN             NaN   
1     NaN      1      1      1          0          NaN             NaN   
2     NaN      1      1      1          0          NaN             NaN   
3     NaN      1      1      1          0          NaN             NaN   
4     NaN      1      1      1         -9          NaN             NaN   

   multiple  success  suicide  attacktype1                 attacktype1_txt  \
0       0.0        1        0            1                   Assassination   
1       0.0        1        0            6     Hostage Taking (Kidnapping)   
2       0.0        1        0            1                   Assassination   
3       0.0        1        0            3               Bombing/Explosion   
4       0.0        1        0            7  Facility/Infrastructure Attack   

   attacktype2 attacktype2_txt  attacktype3 attacktype3_txt  targtype1  \
0          NaN             NaN          NaN             NaN         14   
1          NaN             NaN          NaN             NaN          7   
2          NaN             NaN          NaN             NaN         10   
3          NaN             NaN          NaN             NaN          7   
4          NaN             NaN          NaN             NaN          7   

                 targtype1_txt  targsubtype1  \
0  Private Citizens & Property          68.0   
1      Government (Diplomatic)          45.0   
2          Journalists & Media          54.0   
3      Government (Diplomatic)          46.0   
4      Government (Diplomatic)          46.0   

                                    targsubtype1_txt  \
0                                     Named Civilian   
1  Diplomatic Personnel (outside of embassy, cons...   
2                    Radio Journalist/Staff/Facility   
3                                  Embassy/Consulate   
4                                  Embassy/Consulate   

                         corp1                  target1  natlty1  \
0                          NaN             Julio Guzman     58.0   
1  Belgian Ambassador Daughter  Nadine Chaval, daughter     21.0   
2             Voice of America                 Employee    217.0   
3                          NaN             U.S. Embassy    217.0   
4                          NaN           U.S. Consulate    217.0   

          natlty1_txt  targtype2 targtype2_txt  targsubtype2 targsubtype2_txt  \
0  Dominican Republic        NaN           NaN           NaN              NaN   
1             Belgium        NaN           NaN           NaN              NaN   


In [22]:
# If the data is already combined, read it
if os.path.exists('data/PPT-US_DATA.pkl'):
    df_ppt_DATA = pd.read_pickle('data/PPT-US_DATA.pkl')
    df_ppt_SOURCES = pd.read_pickle('data/PPT-US_SOURCES.pkl')

    
# Otherwise read both files and combine them
elif os.path.exists('data/PPT-US_0517dist.xlsx'):
    # Read data, ignore unicode errors
    df_1 = pd.read_excel('data/PPT-US_0517dist.xlsx', sheet_name= 'DATA')
    df_2 = pd.read_excel('data/PPT-US_0517dist.xlsx', sheet_name= 'SOURCES')
    df_1.to_pickle('data/PPT-US_DATA.pkl')
    df_2.to_pickle('data/PPT-US_SOURCES.pkl')
else:
    print('Data not found, please put data in data folder')

rename some of the  columns

In [23]:
# rename columns
df_ppt_DATA.rename(columns={'DOM_I': 'dominant_ideology', 'I_ETHNO': 'ethno_nationalist',  'I_REL': 'religious', 'I_RACE':  'racist',
                            'I_LEFT': 'extreme_left' , 'I_RIGHT':  'extreme_right', 'G_POL_1':  'politic_reasons', 'G_SOC_1':  'social_reasons',
                            'G_ECO_1': 'economic_reasons', 'G_REL_1':  'religious_reasons'}, inplace=True)

In [24]:
df = df_ppt_DATA[['ORGNAME', 'dominant_ideology']].merge(df_orig, left_on='ORGNAME', right_on='gname', how= 'right')
print(df.shape)

df = df[df['dominant_ideology'].notnull()]
print(df.shape)

(214666, 137)
(7131, 137)


## MAP OF THE DISTRIBUTION OF THE ATTACKS PER GROUPS OVER THE YEAR

- You choose the group/year and you can display the distribution over the globe.
- Can be done for the top 30 groups and include a slide for the group.
- Can be done for all the groups over the years
- PROBLEMS: HOW TO DISPLAY THE GROUPS AND IDENTIFY THEM, SHOULD WE DO A SELECTION? <br>
<br>

The example where  you choose the year and the color represents the dominant ideolgy.

THE DOMINANT IDEOLOGY CATEOGRIES: <br>
-99= Uncertainty/conflicting information exists in available data<br> 
1= Extreme Right Wing (including all racist ideologies)<br>
2= Extreme Left Wing<br>
3= Religious<br>
4= Ethno-nationalist/Separatist<br>
5= Single Issue<br>

In [25]:
fig = px.scatter_geo(df, lat = 'latitude', lon = 'longitude', color="dominant_ideology", animation_frame = 'iyear', projection="natural earth")
fig.show()

the example done for the top 30 groups:

In [26]:
top_groups = df['gname'].value_counts().head(30).index
df_top = df[df['gname'].isin(top_groups)]

In [27]:
fig = px.scatter_geo(df_top, lat = 'latitude', lon = 'longitude', color="iyear", animation_frame = 'gname', projection="natural earth")

fig.show()

## MAP OF THE DISTRIBUTION PER IDEOLOGY
- Not over the years because it’s not very informative, but we can take the dominant ideology category that is found in the PPT_US dataset and plot the distribution over the map.
- PROBLEM: from 214666 datapoint we reduce them to 7131.

## MAP THE FLOW OF OF THE GROUP ATTACKS
- There is the Location of Headquarters in the PPT_US map and we plot the line.
- PROBLEM: little data points.


In [28]:
loc_cols = [col for col in df_ppt_DATA.columns if col.startswith('LOC_HQ')]
df_ppt_DATA.LOC_HQ_COUNTRY_1.unique()

array([-99,   4, 228, 217, 110, 102, 603,  95,  69, 153,  87])

In [29]:
df_ppt_DATA.LOC_HQ_COUNTRY_1
# REPLACE -99 VALUES WITH NAN
df_ppt_DATA[loc_cols] = df_ppt_DATA[loc_cols].replace(-99, np.nan).replace(4, 'Afghanistan').replace(228, 'Yemen').replace(217, 'United States').replace(110, 'Lebanon').replace(102, 'Jordan')
df_ppt_DATA[loc_cols] = df_ppt_DATA[loc_cols].replace(603, 'United Kingdom').replace(95, 'Iraq').replace(69, 'France').replace(153, 'Pakistan').replace(87, 'Haiti')
df_ppt_DATA.LOC_HQ_COUNTRY_1.unique()

array([nan, 'Afghanistan', 'Yemen', 'United States', 'Lebanon', 'Jordan',
       'United Kingdom', 'Iraq', 'France', 'Pakistan', 'Haiti'],
      dtype=object)

In [30]:
# import countries.csv as a df where you can find the coordinates of the centroid  of a state
df_countries = pd.read_csv('data/countries.csv')
df_countries.rename(columns={'longitude': 'hqlon', 'latitude': 'hqlat'}, inplace=True)

In [31]:
df_countries = df_ppt_DATA[['LOC_HQ_COUNTRY_1']].merge(df_countries, left_on='LOC_HQ_COUNTRY_1', right_on='COUNTRY', how='left')[['LOC_HQ_COUNTRY_1', 'hqlon', 'hqlat']]
df_ppt_DATA = df_countries.merge(df_ppt_DATA, on='LOC_HQ_COUNTRY_1', how = 'inner')
df = df_ppt_DATA[['ORGNAME', 'LOC_HQ_COUNTRY_1', 'hqlon', 'hqlat']].merge(df, left_on='ORGNAME', right_on='gname', how= 'inner')
df.head()

ORGNAME_x LOC_HQ_COUNTRY_1  hqlon  hqlat     ORGNAME_y  \
0  Action Squad              NaN    NaN    NaN  Action Squad   
1  Action Squad              NaN    NaN    NaN  Action Squad   
2  Action Squad              NaN    NaN    NaN  Action Squad   
3  Action Squad              NaN    NaN    NaN  Action Squad   
4  Action Squad              NaN    NaN    NaN  Action Squad   

   dominant_ideology       eventid  iyear  imonth  iday approxdate  extended  \
0                2.0  198001260019   1980       1    26        NaN         0   
1                2.0  198001260019   1980       1    26        NaN         0   
2                2.0  198001260019   1980       1    26        NaN         0   
3                2.0  198001260019   1980       1    26        NaN         0   
4                2.0  198001260019   1980       1    26        NaN         0   

  resolution  country    country_txt  region     region_txt provstate  \
0        NaT      217  United States       1  North America  Virginia   
1        NaT      217  United States       1  North America  Virginia   
2        NaT      217  United States       1  North America  Virginia   
3        NaT      217  United States       1  North America  Virginia   
4        NaT      217  United States       1  North America  Virginia   

        city   latitude  longitude  specificity  vicinity  \
0  Arlington  38.878742 -77.100006          1.0         0   
1  Arlington  38.878742 -77.100006          1.0         0   
2  Arlington  38.878742 -77.100006          1.0         0   
3  Arlington  38.878742 -77.100006          1.0         0   
4  Arlington  38.878742 -77.100006          1.0         0   

                                      location  \
0  at residence and vehicle on Highland Street   
1  at residence and vehicle on Highland Street   
2  at residence and vehicle on Highland Street   
3  at residence and vehicle on Highland Street   
4  at residence and vehicle on Highland Street   

                                             summary  crit1  crit2  crit3  \
0  01/26/1980: In Arlington, Virginia, United Sta...      1      1      1   
1  01/26/1980: In Arlington, Virginia, United Sta...      1      1      1   
2  01/26/1980: In Arlington, Virginia, United Sta...      1      1      1   
3  01/26/1980: In Arlington, Virginia, United Sta...      1      1      1   
4  01/26/1980: In Arlington, Virginia, United Sta...      1      1      1   

   doubtterr  alternative alternative_txt  multiple  success  suicide  \
0          0          NaN             NaN       0.0        1        0   
1          0          NaN             NaN       0.0        1        0   
2          0          NaN             NaN       0.0        1        0   
3          0          NaN             NaN       0.0        1        0   
4          0          NaN             NaN       0.0        1        0   

   attacktype1                 attacktype1_txt  attacktype2 attacktype2_txt  \
0            7  Facility/Infrastructure Attack          NaN             NaN   
1            7  Facility/Infrastructure Attack          NaN             NaN   
2            7  Facility/Infrastructure Attack          NaN             NaN   
3            7  Facility/Infrastructure Attack          NaN             NaN   
4            7  Facility/Infrastructure Attack          NaN             NaN   

   attacktype3 attacktype3_txt  targtype1        targtype1_txt  targsubtype1  \
0          NaN             NaN         10  Journalists & Media          53.0   
1          NaN             NaN         10  Journalists & Media          53.0   
2          NaN             NaN         10  Journalists & Media          53.0   
3          NaN             NaN         10  Journalists & Media          53.0   
4          NaN             NaN         10  Journalists & Media          53.0   

                      targsubtype1_txt                corp1  \
0  Newspaper Journalist/Staff/Facility  Tien Phong magazine   
1  Newspaper Journalist/Staff/Facility  Tien Phon

In [32]:
# get dataframe where hqlon is not null
df = df[df['hqlon'].notnull()]
df = df[df['longitude'].notnull()]

df.reset_index(inplace=True, drop=True)

In [33]:
"""fig.add_trace(go.Scattergeo(
    locationmode = 'USA-states',
    lon = df['longitude'],
    lat = df['latitude'],
    #hoverinfo = 'text',
    #text = df_airports['airport'],
    mode = 'markers',
    marker = dict(
        size = 2,
        color = 'rgb(255, 0, 0)',
        line = dict(
            width = 3,
            color = 'rgba(68, 68, 68, 0)'
        )
    )))"""

"fig.add_trace(go.Scattergeo(\n    locationmode = 'USA-states',\n    lon = df['longitude'],\n    lat = df['latitude'],\n    #hoverinfo = 'text',\n    #text = df_airports['airport'],\n    mode = 'markers',\n    marker = dict(\n        size = 2,\n        color = 'rgb(255, 0, 0)',\n        line = dict(\n            width = 3,\n            color = 'rgba(68, 68, 68, 0)'\n        )\n    )))"

In [47]:
# reduce the df only to dominant ideology == 1
df_dom1 = df[df['dominant_ideology'] == 2]
df_dom1.reset_index(inplace=True, drop=True)

In [49]:
import plotly.graph_objects as go

fig = go.Figure()

flight_paths = []
for i in range(len(df_dom1.hqlon)):
    fig.add_trace(
        go.Scattergeo(
            lon = [df_dom1['hqlon'][i], df_dom1['longitude'][i]],
            lat = [df_dom1['hqlat'][i], df_dom1['latitude'][i]],
            mode = 'lines',
            line = dict(width = 1,color = 'red'),
            #opacity = float(df_flight_paths['cnt'][i]) / float(df_flight_paths['cnt'].max()),
        )
    )

fig.update_layout(
    title_text = 'The lines between the HQ of the attack and the attack location for dominant ideology extreme left wing',
    showlegend = False,
    geo = dict(
        scope = 'world',
        projection_type = 'equirectangular',
        showland = True,
        landcolor = 'rgb(243, 243, 243)',
        countrycolor = 'rgb(204, 204, 204)',
        showcountries=True,
    ),
)

fig.show()